In [1]:
import os, glob, re, pickle
from functools import partial
from collections import OrderedDict
import operator as op
from cytoolz import compose

import pyscenic
import pandas as pd
import seaborn as sns
import numpy as np
import scanpy as sc
import anndata as ad
import matplotlib as mpl
import matplotlib.pyplot as plt
#from pyscenic.export import export2loom, add_scenic_metadata
from pyscenic.utils import load_motifs
from pyscenic.transform import df2regulons
from pyscenic.aucell import aucell
from pyscenic.binarization import binarize
from pyscenic.rss import regulon_specificity_scores
from pyscenic.plotting import plot_binarization, plot_rss

from IPython.display import HTML, display

In [2]:
# Set maximum number of jobs for Scanpy.
sc.settings.njobs = 96

Folder structure.

In [3]:
RESOURCES_FOLDERNAME = "/media/ggj/ggjlab2/hezuo/gwh/myeloid/pseudocell/"
AUXILLIARIES_FOLDERNAME = "/media/ggj/ggjlab/pySCENIC_use/"
RESULTS_FOLDERNAME = "/media/ggj/ggjlab2/hezuo/gwh/myeloid/pseudocell/results/"
FIGURES_FOLDERNAME = "/media/ggj/ggjlab2/hezuo/gwh/myeloid/pseudocell/results/figures/"

In [4]:
sc.settings.figdir = FIGURES_FOLDERNAME

Auxilliary functions.

In [5]:
BASE_URL = "http://motifcollections.aertslab.org/v9/logos/"
COLUMN_NAME_LOGO = "MotifLogo"
COLUMN_NAME_MOTIF_ID = "MotifID"
COLUMN_NAME_TARGETS = "TargetGenes"

In [6]:
def savesvg(fname: str, fig, folder: str=FIGURES_FOLDERNAME) -> None:
    """
    Save figure as vector-based SVG image format.
    """
    fig.tight_layout()
    fig.savefig(os.path.join(folder, fname), format='svg')

In [7]:
def display_logos(df: pd.DataFrame, top_target_genes: int = 3, base_url: str = BASE_URL):
    """
    :param df:
    :param base_url:
    """
    # Make sure the original dataframe is not altered.
    df = df.copy()
    
    # Add column with URLs to sequence logo.
    def create_url(motif_id):
        return '<img src="{}{}.png" style="max-height:124px;"></img>'.format(base_url, motif_id)
    df[("Enrichment", COLUMN_NAME_LOGO)] = list(map(create_url, df.index.get_level_values(COLUMN_NAME_MOTIF_ID)))
    
    # Truncate TargetGenes.
    def truncate(col_val):
        return sorted(col_val, key=op.itemgetter(1))[:top_target_genes]
    df[("Enrichment", COLUMN_NAME_TARGETS)] = list(map(truncate, df[("Enrichment", COLUMN_NAME_TARGETS)]))
    
    MAX_COL_WIDTH = pd.get_option('display.max_colwidth')
    pd.set_option('display.max_colwidth', -1)
    display(HTML(df.head().to_html(escape=False)))
    pd.set_option('display.max_colwidth', MAX_COL_WIDTH)

Auxilliary data sets.

In [8]:
# Downloaded fromm pySCENIC github repo: https://github.com/aertslab/pySCENIC/tree/master/resources
DMEL_TFS_FNAME = os.path.join(AUXILLIARIES_FOLDERNAME, 'hh_total_tfs.txt')
# Ranking databases. Downloaded from cisTargetDB: https://resources.aertslab.org/cistarget/
RANKING_DBS_FNAMES = list(map(lambda fn: os.path.join(AUXILLIARIES_FOLDERNAME, fn),
                       ['hg19-tss-centered-10kb-10species.mc9nr.feather',
                       'hg19-500bp-upstream-10species.mc9nr.feather',
                       'hg19-tss-centered-5kb-10species.mc9nr.feather']))
# Motif annotations. Downloaded from cisTargetDB: https://resources.aertslab.org/cistarget/
MOTIF_ANNOTATIONS_FNAME = os.path.join(AUXILLIARIES_FOLDERNAME, 'motifs-v9-nr.hgnc-m0.001-o0.0.tbl')

In [9]:
DATASET_ID = "Macrophage"
#TCGA_CODE = 'SKCM'

Resources downloaded.

In [10]:
# Downloaded from GEO on 28 FEB 2019.
CELL_ANNOTATIONS_FNAME = os.path.join(RESOURCES_FOLDERNAME, "macrophage_pseudocell_20_pheno.csv")
# Downloaded from Cell Journal website on 1 MAR 2019.
#SAMPLE_METADATA_FNAME = os.path.join(RESOURCES_FOLDERNAME, "1-s2.0-S0092867418311784-mmc1.xlsx")
# Downloaded from GEO on 1 MAR 2019.
EXP_MTX_TPM_FNAME = os.path.join(RESOURCES_FOLDERNAME, 'macrophage_pseudocell_20.csv')
#EXP_MTX_COUNTS_FNAME = os.path.join(RESOURCES_FOLDERNAME, 'GSE115978_counts.csv')

Results created.

In [11]:
METADATA_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.metadata.csv'.format(DATASET_ID))
EXP_MTX_QC_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.qc.tpm.csv'.format(DATASET_ID))
ADJACENCIES_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.adjacencies.tsv'.format(DATASET_ID))
MOTIFS_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.motifs.csv'.format(DATASET_ID))
REGULONS_DAT_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.regulons.dat'.format(DATASET_ID))
AUCELL_MTX_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.auc_all.csv'.format(DATASET_ID))
BIN_MTX_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.bin.csv'.format(DATASET_ID))
THR_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.thresholds.csv'.format(DATASET_ID))
ANNDATA_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.h5ad'.format(DATASET_ID))
LOOM_FNAME = os.path.join(RESULTS_FOLDERNAME, '{}.loom'.format(DATASET_ID))

### STEP 0: Preprocessing

__METADATA CLEANING__

In [12]:
df_annotations = pd.read_csv(CELL_ANNOTATIONS_FNAME,index_col=0)
df_annotations

Study_ID      Celltype  \
Pseudocell_Kupffer cell_Cell0    Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell1    Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell10   Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell100  Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell101  Pseudocell_  Kupffer cell   
...                                      ...           ...   
Pseudocell_Macrophage_Cell81     Pseudocell_    Macrophage   
Pseudocell_Macrophage_Cell82     Pseudocell_    Macrophage   
Pseudocell_Macrophage_Cell83     Pseudocell_    Macrophage   
Pseudocell_Macrophage_Cell84     Pseudocell_    Macrophage   
Pseudocell_Macrophage_Cell9      Pseudocell_    Macrophage   

                                                          cellID cluster  \
Pseudocell_Kupffer cell_Cell0      Pseudocell_Kupffer cell_Cell0     NaN   
Pseudocell_Kupffer cell_Cell1      Pseudocell_Kupffer cell_Cell1     NaN   
Pseudocell_Kupffer cell_Cell10    Pseudocell_Kupffer cell_Cell10     NaN   
Pseudocell_Kupffer cell_Cell100  Pseudocell_Kupffer cell_Cell100     NaN   
Pseudocell_Kupffer cell_Cell101  Pseudocell_Kupffer cell_Cell101     NaN   
...                                                          ...     ...   
Pseudocell_Macrophage_Cell81        Pseudocell_Macrophage_Cell81     NaN   
Pseudocell_Macrophage_Cell82        Pseudocell_Macrophage_Cell82     NaN   
Pseudocell_Macrophage_Cell83        Pseudocell_Macrophage_Cell83     NaN   
Pseudocell_Macrophage_Cell84        Pseudocell_Macrophage_Cell84     NaN   
Pseudocell_Macrophage_Cell9          Pseudocell_Macrophage_Cell9     NaN   

                                         type  
Pseudocell_Kupffer cell_Cell0    Kupffer cell  
Pseudocell_Kupffer cell_Cell1    Kupffer cell  
Pseudocell_Kupffer cell_Cell10   Kupffer cell  
Pseudocell_Kupffer cell_Cell100  Kupffer cell  
Pseudocell_Kupffer cell_Cell101  Kupffer cell  
...                                       ...  
Pseudocell_Macrophage_Cell81       Macrophage  
Pseudocell_Macrophage_Cell82       Macrophage  
Pseudocell_Macrophage_Cell83       Macrophage  
Pseudocell_Macrophage_Cell84       Macrophage  
Pseudocell_Macrophage_Cell9        Macrophage  

[883 rows x 5 columns]

In [13]:
#df_annotations['samples'] = df_annotations['samples'].str.upper()
#df_annotations.rename(columns={'cell.types': 'cell_type', 'cells': 'cell_id', 'samples': 'sample_id', 
#                               'treatment.group': 'treatment_group', 'Cohort': 'cohort'}, inplace=True)
#df_annotations['cell_type'] = df_annotations.cell_type.replace({
#    'Mal': 'Malignant Cell',
#    'Endo.': 'Endothelial Cell',
#    'T.CD4': 'Thelper Cell',
#    'CAF': 'Fibroblast',
#    'T.CD8': 'Tcytotoxic Cell',
#    'T.cell': 'T Cell',
#    'NK': 'NK Cell',
#    'B.cell': 'B Cell'})
#df_samples = pd.read_excel(SAMPLE_METADATA_FNAME, header=2)
#df_samples = df_samples.drop(['Cohort'], axis=1)
#df_samples['Sample'] = df_samples.Sample.str.upper()
#df_metadata = pd.merge(df_annotations, df_samples, left_on='sample_id', right_on='Sample')
#df_metadata = df_metadata.drop(['Sample', 'treatment_group'], axis=1)
#df_metadata.rename(columns={'Patient': 'patient_id',
#                           'Age': 'age', 'Sex': 'sex', 'Lesion type': 'lesion_type', 'Site': 'site',
#                           'Treatment': 'treatment', 'Treatment group': 'treatment_group'}, inplace=True)

df_metadata = df_annotations
df_metadata.to_csv(METADATA_FNAME, index=False)
df_metadata.head()

Study_ID      Celltype  \
Pseudocell_Kupffer cell_Cell0    Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell1    Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell10   Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell100  Pseudocell_  Kupffer cell   
Pseudocell_Kupffer cell_Cell101  Pseudocell_  Kupffer cell   

                                                          cellID cluster  \
Pseudocell_Kupffer cell_Cell0      Pseudocell_Kupffer cell_Cell0     NaN   
Pseudocell_Kupffer cell_Cell1      Pseudocell_Kupffer cell_Cell1     NaN   
Pseudocell_Kupffer cell_Cell10    Pseudocell_Kupffer cell_Cell10     NaN   
Pseudocell_Kupffer cell_Cell100  Pseudocell_Kupffer cell_Cell100     NaN   
Pseudocell_Kupffer cell_Cell101  Pseudocell_Kupffer cell_Cell101     NaN   

                                         type  
Pseudocell_Kupffer cell_Cell0    Kupffer cell  
Pseudocell_Kupffer cell_Cell1    Kupffer cell  
Pseudocell_Kupffer cell_Cell10   Kupffer cell  
Pseudocell_Kupffer cell_Cell100  Kupffer cell  
Pseudocell_Kupffer cell_Cell101  Kupffer cell

__EXPRESSION MATRIX QC__

In [14]:
df_tpm = pd.read_csv(EXP_MTX_TPM_FNAME, index_col=0)
df_tpm

Pseudocell_Kupffer cell_Cell0  Pseudocell_Kupffer cell_Cell1  \
A1BG                                 0.000000                       0.000000   
A1CF                                 0.000000                       0.000000   
A2M                                862.425669                    1306.513759   
AAAS                                 0.000000                       0.000000   
AADAC                                0.000000                       0.000000   
...                                       ...                            ...   
RP11-501J20.5                        0.000000                       0.000000   
RP3-406P24.4                         0.000000                       0.000000   
NPPA                                 0.000000                       0.000000   
RP11-302F12.10                       0.000000                       0.000000   
RP11-521D12.5                        0.000000                       0.000000   

                Pseudocell_Kupffer cell_Cell10  \
A1BG                                  0.000000   
A1CF                                  0.000000   
A2M                                1181.701367   
AAAS                                  0.000000   
AADAC                                 0.000000   
...                                        ...   
RP11-501J20.5                         0.000000   
RP3-406P24.4                          0.000000   
NPPA                                  0.000000   
RP11-302F12.10                        0.000000   
RP11-521D12.5                         0.000000   

                Pseudocell_Kupffer cell_Cell100  \
A1BG                                   0.000000   
A1CF                                   0.000000   
A2M                                  530.484013   
AAAS                                  57.012543   
AADAC                                  0.000000   
...                                         ...   
RP11-501J20.5                          0.000000   
RP3-406P24.4                           0.000000   
NPPA                                   0.000000   
RP11-302F12.10                         0.000000   
RP11-521D12.5                          0.000000   

                Pseudocell_Kupffer cell_Cell101  \
A1BG                                    0.00000   
A1CF                                    0.00000   
A2M                                   826.07104   
AAAS                                    0.00000   
AADAC                                   0.00000   
...                                         ...   
RP11-501J20.5                           0.00000   
RP3-406P24.4                            0.00000   
NPPA                                    0.00000   
RP11-302F12.10                          0.00000   
RP11-521D12.5                           0.00000   

                Pseudocell_Kupffer cell_Cell102  \
A1BG                                   0.000000   
A1CF                                   0.000000   
A2M                                  881.558583   
AAAS                                   0.000000   
AADAC                                 67.204301   
...                                         ...   
RP11-501J20.5                          0.000000   
RP3-406P24.4                           0.000000   
NPPA                                   0.000000   
RP11-302F12.10                         0.000000   
RP11-521D12.5                          0.000000   

                Pseudocell_Kupffer cell_Cell103  \
A1BG                                   0.000000   
A1CF                                   0.000000   
A2M                                 1062.869325   
AAAS                                   0.000000   
AADAC                                  0.000000   
...                                         ...   
RP11-501J20.5                          0.000000   
RP3-406P24.4                           0.000000   
NPPA                                   0.000000   
RP11-302F12.10                         0.000000   
RP11-521D12.5                          0.000000   

  

In [15]:
#df_counts = pd.read_csv(EXP_MTX_COUNTS_FNAME, index_col=0)
#df_counts.shape

In [16]:
adata = sc.AnnData(X=df_tpm.T.sort_index())
df_obs = df_metadata[['Celltype','type','cellID']].set_index('cellID').sort_index()
adata.obs = df_obs
adata.var_names_make_unique()
sc.pp.filter_cells(adata, min_genes=0)
sc.pp.filter_genes(adata, min_cells=0)
# Store non-log transformed data as raw. This data can be used via the use_raw parameters available for many functions.
# In the scanpy's tutorials this is used to stored all genes in log-transformed counts before retaining only Highly Variable Genes (HVG). 
# Because in this case no filtering is done we use this feature to store raw counts.
adata.raw = adata 
sc.pp.log1p(adata)
adata

AnnData object with n_obs × n_vars = 883 × 19061
    obs: 'Celltype', 'type', 'n_genes'
    var: 'n_cells'
    uns: 'log1p'

In [17]:
adata.write_h5ad(ANNDATA_FNAME) # Categorical dtypes are created.

... storing 'Celltype' as categorical
... storing 'type' as categorical


In [18]:
adata.to_df().to_csv(EXP_MTX_QC_FNAME)

### STEP 1: Network inference based on GRNBoost2 from CLI

For this step the CLI version of SCENIC is used. This step can be deployed on an High Performance Computing system.

_Output:_ List of adjacencies between a TF and its targets stored in `ADJACENCIES_FNAME`.

need env:pyscenic

In [19]:
!pyscenic grn {EXP_MTX_QC_FNAME} {DMEL_TFS_FNAME} -o {ADJACENCIES_FNAME} --num_workers 24


2021-12-07 21:58:18,822 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.

2021-12-07 21:58:27,143 - pyscenic.cli.pyscenic - INFO - Inferring regulatory networks.
/home/ggj/anaconda3/lib/python3.8/site-packages/distributed/node.py:151: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 38503 instead
  warnings.warn(
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a non-main thread, the TBB library may be in an invalid state in the child process.
Numba: Attempted to fork from a no

In [12]:
import pyscenic
import dask
print(pyscenic.__version__)
print(dask.__version__)

0.10.3
1.0.0


```
2019-04-25 11:22:20,360 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.
2019-04-25 11:23:37,612 - pyscenic.cli.pyscenic - INFO - Inferring regulatory networks.
preparing dask client
parsing input
creating dask graph
4 partitions
computing dask graph
not shutting down client, client was created externally
finished
2019-04-26 03:58:01,096 - pyscenic.cli.pyscenic - INFO - Writing results to file.
```

### STEP 2-3: Regulon prediction aka cisTarget from CLI

For this step the CLI version of SCENIC is used. This step can be deployed on an High Performance Computing system.

_Output:_ List of adjacencies between a TF and its targets stored in `MOTIFS_FNAME`.

In [12]:
DBS_PARAM = ' '.join(RANKING_DBS_FNAMES)
DBS_PARAM

'/media/ggj/ggjlab/pySCENIC_use/hg19-tss-centered-10kb-10species.mc9nr.feather /media/ggj/ggjlab/pySCENIC_use/hg19-500bp-upstream-10species.mc9nr.feather /media/ggj/ggjlab/pySCENIC_use/hg19-tss-centered-5kb-10species.mc9nr.feather'

In [13]:
!pyscenic ctx {ADJACENCIES_FNAME} {DBS_PARAM} \
            --annotations_fname {MOTIF_ANNOTATIONS_FNAME} \
            --expression_mtx_fname {EXP_MTX_QC_FNAME} \
            --output {MOTIFS_FNAME} \
            --num_workers 4


2021-12-07 22:09:24,629 - pyscenic.cli.pyscenic - INFO - Creating modules.

2021-12-07 22:09:25,491 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.

2021-12-07 22:09:33,996 - pyscenic.utils - INFO - Calculating Pearson correlations.

2021-12-07 22:09:34,498 - pyscenic.utils - WARNING - Note on correlation calculation: the default behaviour for calculating the correlations has changed after pySCENIC verion 0.9.16. Previously, the default was to calculate the correlation between a TF and target gene using only cells with non-zero expression values (mask_dropouts=True). The current default is now to use all cells to match the behavior of the R verision of SCENIC. The original settings can be retained by setting 'rho_mask_dropouts=True' in the modules_from_adjacencies function, or '--mask_dropouts' from the CLI.
	Dropout masking is currently set to [False].

2021-12-07 22:10:02,974 - pyscenic.utils - INFO - Creating modules.

2021-12-07 22:13:03,741 - pyscenic.cli.pyscenic - I


2021-12-07 22:13:31,321 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for AKNA could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 26.3s
2021-12-07 22:13:31,376 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for LEF1 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 26.9s
2021-12-07 22:13:31,969 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HES5 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.

2021-12-07 22:13:31,970 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for E2F6 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.

2021-12-07 22:13:32,021 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for AR could be mapped to hg19

[                                        ] | 0% Completed | 33.4s
2021-12-07 22:13:38,425 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for LYL1 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 33.6s
2021-12-07 22:13:38,590 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HIC1 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.

2021-12-07 22:13:38,664 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for MAEL could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 33.7s
2021-12-07 22:13:38,772 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HIC2 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 3


2021-12-07 22:13:51,796 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for ETV4 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 47.0s
2021-12-07 22:13:52,086 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HOXB7 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.

2021-12-07 22:13:52,090 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for MBD3 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 47.1s
2021-12-07 22:13:52,193 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HOXC4 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 47.2s
2021-12-07 22:13:52,257 - pyscenic.transform - WARNING - L

[                                        ] | 0% Completed | 51.3s
2021-12-07 22:13:56,438 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for MEIS2 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 51.4s
2021-12-07 22:13:56,439 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for BAZ2B could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed | 51.5s
2021-12-07 22:13:56,545 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for MESP1 could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.

2021-12-07 22:13:56,568 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for BBX could be mapped to hg19-tss-centered-10kb-10species.mc9nr. Skipping this module.
[                                        ] | 0% Completed |

...

[####################################### ] | 97% Completed | 37min 40.8s
2021-12-07 22:50:45,806 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for ZNF432 could be mapped to hg19-500bp-upstream-10species.mc9nr. Skipping this module.

2021-12-07 22:50:45,827 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HES4 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.

2021-12-07 22:50:45,883 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for ZNF433 could be mapped to hg19-500bp-upstream-10species.mc9nr. Skipping this module.
[####################################### ] | 97% Completed | 37min 40.9s
2021-12-07 22:50:45,925 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HES5 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 97% Completed | 37min 41.0s
2021-12-07 22:50:46,031 - pyscenic.transfor

[####################################### ] | 98% Completed | 37min 44.0s
2021-12-07 22:50:49,118 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HLX could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 44.1s
2021-12-07 22:50:49,209 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HMBOX1 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 44.2s
2021-12-07 22:50:49,306 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HMG20A could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 44.3s
2021-12-07 22:50:49,410 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HMG20B could be mapped to hg19-tss-centered-5kb-10spec

[####################################### ] | 98% Completed | 37min 48.4s
2021-12-07 22:50:53,455 - pyscenic.transform - WARNING - Less than 80% of the genes in Regulon for HNF1B could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 48.9s
2021-12-07 22:50:53,970 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF143 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 49.1s
2021-12-07 22:50:54,187 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF146 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 49.3s
2021-12-07 22:50:54,386 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF148 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[

[####################################### ] | 98% Completed | 37min 52.0s
2021-12-07 22:50:57,099 - pyscenic.transform - WARNING - Less than 80% of the genes in TFDP2 could be mapped to hg19-500bp-upstream-10species.mc9nr. Skipping this module.

2021-12-07 22:50:57,099 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF197 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 52.1s
2021-12-07 22:50:57,242 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF2 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 52.2s
2021-12-07 22:50:57,353 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF20 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 52.4s
2021-12-07 22:50:

[####################################### ] | 98% Completed | 37min 55.8s
2021-12-07 22:51:00,905 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF230 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 55.9s
2021-12-07 22:51:01,068 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF232 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 56.2s
2021-12-07 22:51:01,183 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF233 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[####################################### ] | 98% Completed | 37min 56.3s
2021-12-07 22:51:01,330 - pyscenic.transform - WARNING - Less than 80% of the genes in ZNF234 could be mapped to hg19-tss-centered-5kb-10species.mc9nr. Skipping this module.
[###########

```
2019-04-26 10:23:50,395 - pyscenic.cli.pyscenic - INFO - Creating modules.
2019-04-26 10:23:56,229 - pyscenic.cli.pyscenic - INFO - Loading expression matrix.
2019-04-26 10:29:09,101 - pyscenic.cli.pyscenic - INFO - Loading databases.
2019-04-26 10:29:09,101 - pyscenic.cli.pyscenic - INFO - Calculating regulons.
2019-04-26 11:11:10,784 - pyscenic.cli.pyscenic - INFO - Writing results to file
```

The results is a list of enriched motifs for the modules.

| Column name | Description |
| ----------- | ----------- |
| TF | Transcription Factor (TF) for which an enriched motif is discovered. |
| motifID | The identifier of the enriched motif. |
| AUC | Area Under the recovery Curve statistic for this enriched motif. |
| NES | Normalized Enrichment Score for this enriched motif. |
| Context | Collection of tags clarifying the origin of the module for this factor: e.g. ranking database, ... |
| Annotation | Verbose description of the annotation available for this motif. |
| MotifSimilarityQvalue | The TomTom derived Q-value for motif similarity (if used for assigning the factor to this enriched motif). |
| OrthologousIdentity | The Amino Acid Identity between factors (if used for assigning the factor to this enriched motif). |
| RankAtMax | The position of the Leading Edge which is used as a threshold on the whole genome ranking of the motif to decide if a gene in the input is a direct target of a TF that binds this motif. |
| TargetGenes | A list of pairs: genes and their associated weights from GENIE3/GRNBoost2. |

In [14]:
df_motifs = load_motifs(MOTIFS_FNAME)

In [15]:
df_motifs.head()

Enrichment            \
                                                   AUC       NES   
TF   MotifID                                                       
ATF3 transfac_pro__M08931                     0.047173  3.483106   
     taipale_cyt_meth__XBP1_NRTGACGTCAYN_FL   0.047169  3.482373   
     dbcorrdb__JUN__ENCSR000EGH_1__m1         0.049270  3.865721   
     dbcorrdb__JUND__ENCSR000EGN_1__m1        0.052179  4.396326   
     dbcorrdb__BCL3__ENCSR000BQH_1__m2        0.047827  3.602524   

                                                                   \
                                            MotifSimilarityQvalue   
TF   MotifID                                                        
ATF3 transfac_pro__M08931                                0.000007   
     taipale_cyt_meth__XBP1_NRTGACGTCAYN_FL              0.000000   
     dbcorrdb__JUN__ENCSR000EGH_1__m1                    0.000011   
     dbcorrdb__JUND__ENCSR000EGN_1__m1                   0.000045   
     dbcorrdb__BCL3__ENCSR000BQH_1__m2                   0.000006   

                                                                 \
                                            OrthologousIdentity   
TF   MotifID                                                      
ATF3 transfac_pro__M08931                              1.000000   
     taipale_cyt_meth__XBP1_NRTGACGTCAYN_FL            1.000000   
     dbcorrdb__JUN__ENCSR000EGH_1__m1                  1.000000   
     dbcorrdb__JUND__ENCSR000EGN_1__m1                 1.000000   
     dbcorrdb__BCL3__ENCSR000BQH_1__m2                 0.950276   

                                                                                                \
                                                                                    Annotation   
TF   MotifID                                                                                     
ATF3 transfac_pro__M08931                    gene is annotated for similar motif homer__DAT...   
     taipale_cyt_meth__XBP1_NRTGACGTCAYN_FL  motif similar to taipale_cyt_meth__ATF3_NRTGAY...   
     dbcorrdb__JUN__ENCSR000EGH_1__m1        gene is annotated for similar motif homer__DAT...   
     dbcorrdb__JUND__ENCSR000EGN_1__m1       gene is annotated for similar motif homer__DAT...   
     dbcorrdb__BCL3__ENCSR000BQH_1__m2       gene is orthologous to ENSMUSG00000026628 in M...   

                                                                                                \
                                                                                       Context   
TF   MotifID                                                                                     
ATF3 transfac_pro__M08931                    (hg19-tss-centered-10kb-10species.mc9nr, weigh...   
     taipale_cyt_meth__XBP1_NRTGACGTCAYN_FL  (hg19-tss-centered-10kb-10species.mc9nr, weigh...   
     dbcorrdb__JUN__ENCSR000EGH_1__m1        (hg19-tss-centered-10kb-10species.mc9nr, weigh...   
     dbcorrdb__JUND__ENCSR000EGN_1__m1       (hg19-tss-centered-10kb-10species.mc9nr, weigh...   
     dbcorrdb__BCL3__ENCSR000BQH_1__m2       (hg19-tss-centered-10kb-10species.mc9nr, weigh...   

                                                                                                \
                                                                                   TargetGenes   
TF   MotifID                                                                                     
ATF3 transfac_pro__M08931                    [(ANXA1, 8.119254806729975), (JUNB, 15.5803696...   
     taipale_cyt_meth__XBP1_NRTGACGTCAYN_FL  [(NR4A3, 13.211473964257786), (JUN, 10.1593691...   
     dbcorrdb__JUN__ENCSR000EGH_1__m1        [(LMNA, 4.7349171865662765), (H3F3B, 18.031004...   
     dbcorrdb__JUND__ENCSR000EGN_1__m1       [(LMNA, 4.7349171865662765), (HSPA5, 0.8687054...   
     dbcorrdb__BCL3__ENCSR000BQH_1__m2       [(KDM6B, 0.8269039400798083), (ANTXR2, 1.06126...   

                                                      

Display the enriched motifs with their associated sequence logos.

In [16]:
display_logos(df_motifs.head())

/home/ggj/anaconda3/envs/pyscenic/lib/python3.6/site-packages/ipykernel_launcher.py:20: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.


### STEP 4: Cellular enrichment aka AUCell

__REGULON CREATION__

Regulons can easily be created from this list of enriched motifs via `pyscenic.transform.df2regulons`. Here we provide an auxilliary function to carefully select the enriched motifs that contribute to the regulons.

In [17]:
def derive_regulons(motifs, db_names=('mm9-tss-centered-5kb-10species','mm9-tss-centered-10kb-7species','mm9-500bp-upstream-7species')):
    motifs.columns = motifs.columns.droplevel(0)

    def contains(*elems):
        def f(context):
            return any(elem in context for elem in elems)
        return f

    # For the creation of regulons we only keep the 10-species databases and the activating modules. We also remove the
    # enriched motifs for the modules that were created using the method 'weight>50.0%' (because these modules are not part
    # of the default settings of modules_from_adjacencies anymore.
    motifs = motifs[
        np.fromiter(map(compose(op.not_, contains('weight>50.0%')), motifs.Context), dtype=np.bool) & \
       # np.fromiter(map(contains(*db_names), motifs.Context), dtype=np.bool) & \
        np.fromiter(map(contains('activating'), motifs.Context), dtype=np.bool)]

    # We build regulons only using enriched motifs with a NES of 1.0 or higher; 
    #we take only directly annotated TFs or TF annotated
    # for an orthologous gene into account; and we only keep regulons with at least 1 genes.
    regulons = list(filter(lambda r: len(r) >= 1, df2regulons(motifs[(motifs['NES'] >= 1.0) 
                                                                      & ((motifs['Annotation'] == 'gene is directly annotated')
                                                                        | (motifs['Annotation'].str.startswith('gene is orthologous to')
                                                                           & motifs['Annotation'].str.endswith('which is directly annotated for motif')))
                                                                     ])))
    
    # Rename regulons, i.e. remove suffix.
    return list(map(lambda r: r.rename(r.transcription_factor), regulons))

In [18]:
regulons = derive_regulons(df_motifs)

Create regulons from a dataframe of enriched features.
Additional columns saved: []


In [17]:
import pyscenic

In [18]:
regulons=pyscenic.transform.df2regulons(df_motifs)

Create regulons from a dataframe of enriched features.
Additional columns saved: []


In [19]:
# Pickle these regulons.
with open(REGULONS_DAT_FNAME, 'wb') as f:
    pickle.dump(regulons, f)

In [20]:
len(regulons)

98

In [21]:
regulons

[Regulon(name='AHR(+)', gene2weight=frozendict({'EMP1': 0.8927042305443323, 'MMP9': 1.1312360255374667, 'NR4A3': 0.8358165996558687, 'SLC25A37': 2.1767126738661435, 'SGK3': 0.7914471829555907, 'THSD4': 0.8328222991739895, 'AICDA': 1.1140855886771464, 'F13A1': 1.5216720756671596, 'EPS8L3': 0.6963987417017128, 'ENO1': 1.4859186159362752, 'LRFN4': 1.5130682746697954, 'ATF2': 0.6868749666383618, 'RPL11': 0.6993016506706556, 'PGAM1': 0.9318722618297902, 'CLSTN2': 0.9423958158975104, 'DLGAP4': 0.6909100687102491, 'PPP1R3B': 1.0197124472533938, 'ACIN1': 0.7974730920400691}), gene2occurrence=frozendict({}), transcription_factor='AHR', context=frozenset({'cisbp__M5236.png', 'activating'}), score=1.2081796494200694, nes=0.0, orthologous_identity=0.0, similarity_qvalue=0.0, annotation=''),
 Regulon(name='ATF3(+)', gene2weight=frozendict({'ANXA1': 8.119254806729975, 'JUNB': 15.580369613013065, 'LMNA': 4.7349171865662765, 'HMGA1': 3.6623301763503635, 'H3F3B': 18.031004502683952, 'CD109': 5.28282782

In [22]:
# Pickle these regulons.
with open(REGULONS_DAT_FNAME, 'wb') as f:
    pickle.dump(regulons, f)

__AUCELL__

In [23]:
df_raw = pd.read_csv("/media/ggj/ggjlab2/hezuo/gwh/myeloid/pseudocell/macrophage_dge.csv", index_col=0)

In [24]:
df_raw

Liver7S2.TTCATAAGATGGTAGAGA  Liver7S2.TCGTAAAAAACGCCGACG  \
A1BG                                      0                            0   
A1CF                                      0                            0   
A2M                                       0                            2   
AAAS                                      0                            0   
AADAC                                     0                            0   
...                                     ...                          ...   
RP11-501J20.5                             0                            0   
RP3-406P24.4                              0                            0   
NPPA                                      0                            0   
RP11-302F12.10                            0                            0   
RP11-521D12.5                             0                            0   

                Liver7S2.GCAGGAGCTCAAACGAGC  Liver7S2.ATCTCTAAAACGGACACT  \
A1BG                                      0                            0   
A1CF                                      0                            0   
A2M                                       5                            1   
AAAS                                      0                            0   
AADAC                                     0                            0   
...                                     ...                          ...   
RP11-501J20.5                             0                            0   
RP3-406P24.4                              0                            0   
NPPA                                      0                            0   
RP11-302F12.10                            0                            0   
RP11-521D12.5                             0                            0   

                Liver7S2.ATGCTTGGACATATTCCA  Liver7S2.GGACATTGATCAGATCTT  \
A1BG                                      0                            0   
A1CF                                      0                            0   
A2M                                       0                            0   
AAAS                                      0                            0   
AADAC                                     0                            0   
...                                     ...                          ...   
RP11-501J20.5                             0                            0   
RP3-406P24.4                              0                            0   
NPPA                                      0                            0   
RP11-302F12.10                            0                            0   
RP11-521D12.5                             0                            0   

                Liver7S2.ACGAGCATACAGAGGGTC  Liver7S2.CATGATAAAGTTTGCGGA  \
A1BG                                      0                            0   
A1CF                                      0                            0   
A2M                                       0                            1   
AAAS                                      0                            0   
AADAC                                     0                            0   
...                                     ...                          ...   
RP11-501J20.5                             0                            0   
RP3-406P24.4                              0                            0   
NPPA                                      0                            0   
RP11-302F12.10                            0                            0   
RP11-521D12.5                             0                            0   

                Liver7S2.AGTCGTGGGCGACGGCAG  Liver7S2.GGTACACCGCTAGCTCAA  ...  \
A1BG                                      0                            0  ...   
A1CF                                      0                            0  ...   
A2M                                       1                            1  ...   
AAAS                                    

In [25]:
adata = sc.AnnData(X=df_raw.T)
#df_obs = df_metadata[['Celltype','cluster','type','cellID']].set_index('cellID').sort_index()
#adata.obs = df_obs
adata.var_names_make_unique()
sc.pp.filter_cells(adata, min_genes=0)
sc.pp.filter_genes(adata, min_cells=0)
# Store non-log transformed data as raw. This data can be used via the use_raw parameters available for many functions.
# In the scanpy's tutorials this is used to stored all genes in log-transformed counts before retaining only Highly Variable Genes (HVG). 
# Because in this case no filtering is done we use this feature to store raw counts.
adata.raw = adata 
sc.pp.log1p(adata)
adata

AnnData object with n_obs × n_vars = 17626 × 19061
    obs: 'n_genes'
    var: 'n_cells'
    uns: 'log1p'

In [26]:
df_tpm=adata.to_df()

In [27]:
df_tpm

A1BG  A1CF       A2M  AAAS  AADAC  AADAT  AAED1  \
Liver7S2.TTCATAAGATGGTAGAGA   0.0   0.0  0.000000   0.0    0.0    0.0    0.0   
Liver7S2.TCGTAAAAAACGCCGACG   0.0   0.0  1.098612   0.0    0.0    0.0    0.0   
Liver7S2.GCAGGAGCTCAAACGAGC   0.0   0.0  1.791759   0.0    0.0    0.0    0.0   
Liver7S2.ATCTCTAAAACGGACACT   0.0   0.0  0.693147   0.0    0.0    0.0    0.0   
Liver7S2.ATGCTTGGACATATTCCA   0.0   0.0  0.000000   0.0    0.0    0.0    0.0   
...                           ...   ...       ...   ...    ...    ...    ...   
ICC3AD.CCGCTAGCTGTGAACCTA     0.0   0.0  0.000000   0.0    0.0    0.0    0.0   
ICC3AD.AAGCGGGTCGGTGCAGGA     0.0   0.0  0.000000   0.0    0.0    0.0    0.0   
ICC3AD.ATCTCTGGACATAAGTAC     0.0   0.0  0.000000   0.0    0.0    0.0    0.0   
ICC3AD.CTGTGTACTTATGACACT     0.0   0.0  0.000000   0.0    0.0    0.0    0.0   
ICC3AD.TGCGGATATTGTAGTTTA     0.0   0.0  0.693147   0.0    0.0    0.0    0.0   

                             AAGAB  AAK1  AAMDC  ...  DBH  LY6G5B  \
Liver7S2.TTCATAAGATGGTAGAGA    0.0   0.0    0.0  ...  0.0     0.0   
Liver7S2.TCGTAAAAAACGCCGACG    0.0   0.0    0.0  ...  0.0     0.0   
Liver7S2.GCAGGAGCTCAAACGAGC    0.0   0.0    0.0  ...  0.0     0.0   
Liver7S2.ATCTCTAAAACGGACACT    0.0   0.0    0.0  ...  0.0     0.0   
Liver7S2.ATGCTTGGACATATTCCA    0.0   0.0    0.0  ...  0.0     0.0   
...                            ...   ...    ...  ...  ...     ...   
ICC3AD.CCGCTAGCTGTGAACCTA      0.0   0.0    0.0  ...  0.0     0.0   
ICC3AD.AAGCGGGTCGGTGCAGGA      0.0   0.0    0.0  ...  0.0     0.0   
ICC3AD.ATCTCTGGACATAAGTAC      0.0   0.0    0.0  ...  0.0     0.0   
ICC3AD.CTGTGTACTTATGACACT      0.0   0.0    0.0  ...  0.0     0.0   
ICC3AD.TGCGGATATTGTAGTTTA      0.0   0.0    0.0  ...  0.0     0.0   

                             RP1-15D23.2  RP11-174N3.4  RP11-37N22.1  \
Liver7S2.TTCATAAGATGGTAGAGA          0.0           0.0           0.0   
Liver7S2.TCGTAAAAAACGCCGACG          0.0           0.0           0.0   
Liver7S2.GCAGGAGCTCAAACGAGC          0.0           0.0           0.0   
Liver7S2.ATCTCTAAAACGGACACT          0.0           0.0           0.0   
Liver7S2.ATGCTTGGACATATTCCA          0.0           0.0           0.0   
...                                  ...           ...           ...   
ICC3AD.CCGCTAGCTGTGAACCTA            0.0           0.0           0.0   
ICC3AD.AAGCGGGTCGGTGCAGGA            0.0           0.0           0.0   
ICC3AD.ATCTCTGGACATAAGTAC            0.0           0.0           0.0   
ICC3AD.CTGTGTACTTATGACACT            0.0           0.0           0.0   
ICC3AD.TGCGGATATTGTAGTTTA            0.0           0.0           0.0   

                             RP11-501J20.5  RP3-406P24.4  NPPA  \
Liver7S2.TTCATAAGATGGTAGAGA            0.0           0.0   0.0   
Liver7S2.TCGTAAAAAACGCCGACG            0.0           0.0   0.0   
Liver7S2.GCAGGAGCTCAAACGAGC            0.0           0.0   0.0   
Liver7S2.ATCTCTAAAACGGACACT            0.0           0.0   0.0   
Liver7S2.ATGCTTGGACATATTCCA            0.0           0.0   0.0   
...                                    ...           ...   ...   
ICC3AD.CCGCTAGCTGTGAACCTA              0.0           0.0   0.0   
ICC3AD.AAGCGGGTCGGTGCAGGA              0.0           0.0   0.0   
ICC3AD.ATCTCTGGACATAAGTAC              0.0           0.0   0.0   
ICC3AD.CTGTGTACTTATGACACT              0.0           0.0   0.0   
ICC3AD.TGCGGATATTGTAGTTTA              0.0           0.0   0.0   

                             RP11-302F12.10  RP11-521D12.5  
Liver7S2.TTCATAAGATGGTAGAGA             0.0            0.0  
Liver7S2.TCGTAAAAAACGCCGACG             0.0            0.0  
Liver7S2.GCAGGAGCTCAAACGAGC             0.0            0.0  
Liver7S2.ATCTCTAAAACGGACACT             0.0            0.0  
Liver7S2.ATGCTTGGACATATTCCA             0.0            0.0  
...                                     ...            ...  
ICC3AD.CCGCTAGCTGTGAACCTA               0.0            0.0  
ICC3AD.AAGCGGGTCGGTGCAGGA               0.0            0.0  
ICC3AD.ATCTCTGGACATAAGTAC       

In [24]:
del df_raw

In [25]:
#sc.pp.subsample(df_raw,fraction=0.5)

In [28]:
%%time
auc_mtx = aucell(df_tpm, regulons, num_workers=4)
auc_mtx.to_csv(AUCELL_MTX_FNAME)

CPU times: user 12.8 s, sys: 10.3 s, total: 23.1 s
Wall time: 33.7 s


```
CPU times: user 23.1 s, sys: 10.7 s, total: 33.8 s
Wall time: 39.2 s
```

In [42]:
auc_mtx = pd.read_csv(AUCELL_MTX_FNAME, index_col=0)

In [12]:
auc_mtx=pd.read_csv("../results/AUCELL.csv",index_col=0)

In [43]:
auc_mtx

ATF3(+)   ATF4(+)   ATF5(+)  BACH1(+)  \
Cell                                                                  
Liver7S2.TTCATAAGATGGTAGAGA  0.190630  0.123316  0.119214  0.065176   
Liver7S2.TCGTAAAAAACGCCGACG  0.168980  0.127585  0.088205  0.072158   
Liver7S2.GCAGGAGCTCAAACGAGC  0.150117  0.091940  0.083466  0.060028   
Liver7S2.ATCTCTAAAACGGACACT  0.168490  0.105839  0.095441  0.045695   
Liver7S2.CTCGCACACAAGCCTAGA  0.249478  0.156324  0.187428  0.051390   
...                               ...       ...       ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA    0.114718  0.091260  0.071707  0.037861   
ICC3AD.AAGCGGGTCGGTGCAGGA    0.117059  0.096923  0.086141  0.076030   
ICC3AD.ATCTCTGGACATAAGTAC    0.099506  0.083185  0.067867  0.020159   
ICC3AD.CTGTGTACTTATGACACT    0.117478  0.121020  0.070050  0.024672   
ICC3AD.TGCGGATATTGTAGTTTA    0.123725  0.121024  0.091433  0.043285   

                             BCLAF1(+)  BHLHE40(+)  BHLHE41(+)  CEBPA(+)  \
Cell                                                                       
Liver7S2.TTCATAAGATGGTAGAGA   0.022979    0.208645    0.000000  0.005869   
Liver7S2.TCGTAAAAAACGCCGACG   0.021929    0.176737    0.000000  0.013004   
Liver7S2.GCAGGAGCTCAAACGAGC   0.024562    0.149326    0.000000  0.001809   
Liver7S2.ATCTCTAAAACGGACACT   0.028297    0.186483    0.000000  0.028571   
Liver7S2.CTCGCACACAAGCCTAGA   0.025726    0.211125    0.062223  0.021359   
...                                ...         ...         ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA     0.025260    0.109823    0.000000  0.008217   
ICC3AD.AAGCGGGTCGGTGCAGGA     0.039742    0.085635    0.000000  0.015346   
ICC3AD.ATCTCTGGACATAAGTAC     0.028386    0.089461    0.000000  0.023656   
ICC3AD.CTGTGTACTTATGACACT     0.029964    0.091671    0.000000  0.006436   
ICC3AD.TGCGGATATTGTAGTTTA     0.027951    0.162256    0.000000  0.040225   

                             CEBPB(+)  CEBPD(+)  ...  THAP11(+)   UBP1(+)  \
Cell                                             ...                        
Liver7S2.TTCATAAGATGGTAGAGA  0.112141  0.145144  ...   0.015195  0.000000   
Liver7S2.TCGTAAAAAACGCCGACG  0.082778  0.165620  ...   0.025757  0.000000   
Liver7S2.GCAGGAGCTCAAACGAGC  0.095875  0.156474  ...   0.023694  0.000000   
Liver7S2.ATCTCTAAAACGGACACT  0.098958  0.118451  ...   0.029764  0.000000   
Liver7S2.CTCGCACACAAGCCTAGA  0.034196  0.037709  ...   0.019850  0.000000   
...                               ...       ...  ...        ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA    0.044278  0.052852  ...   0.051960  0.038188   
ICC3AD.AAGCGGGTCGGTGCAGGA    0.031974  0.076218  ...   0.025985  0.000000   
ICC3AD.ATCTCTGGACATAAGTAC    0.036186  0.074820  ...   0.023677  0.000000   
ICC3AD.CTGTGTACTTATGACACT    0.042843  0.022416  ...   0.021288  0.000000   
ICC3AD.TGCGGATATTGTAGTTTA    0.041552  0.041227  ...   0.028049  0.000000   

                              UBTF(+)   USF2(+)   XBP1(+)   ZEB2(+)  ZMIZ1(+)  \
Cell                                                                            
Liver7S2.TTCATAAGATGGTAGAGA  0.049331  0.064463  0.124954  0.214933  0.045662   
Liver7S2.TCGTAAAAAACGCCGACG  0.085850  0.074552  0.070051  0.206262  0.043500   
Liver7S2.GCAGGAGCTCAAACGAGC  0.089068  0.068583  0.000000  0.164783  0.039130   
Liver7S2.ATCTCTAAAACGGACACT  0.003934  0.071982  0.072500  0.125209  0.055967   
Liver7S2.CTCGCACACAAGCCTAGA  0.016528  0.057799  0.130757  0.000000  0.056864   
...                               ...       ...       ...       ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA    0.055584  0.034892  0.030918  0.000305  0.040978   
ICC3AD.AAGCGGGTCGGTGCAGGA    0.046210  0.031102  0.125998  0.000000  0.051482   
ICC3AD.ATCTCTGGACATAAGTAC    0.080576  0.053043  0.031412  0.001832  0.039308   
ICC3AD.CTGTGTACTTATGACACT    0.048565  0.034591  0.113005  0.000000  0.025111   
ICC3AD.TGCGGATATTGTAGTTTA    0.048602  0.037054  0.029437  0.115523  0.024537   

                             ZNF136(+)  ZNF420(+)  ZNF528(+) 

In [58]:
#pd.DataFrame(auc_mtx.index).to_csv("./results/sample_cellname.csv")

__CELL TYPE SPECIFIC REGULATORS - RSS__

In [29]:
auc_mtx

Regulon                        AHR(+)   ATF3(+)   ATF4(+)   ATF5(+)  BACH1(+)  \
Cell                                                                            
Liver7S2.TTCATAAGATGGTAGAGA  0.123182  0.224860  0.145770  0.067380  0.000000   
Liver7S2.TCGTAAAAAACGCCGACG  0.006728  0.191543  0.102517  0.051133  0.029175   
Liver7S2.GCAGGAGCTCAAACGAGC  0.070282  0.156045  0.104557  0.048152  0.014069   
Liver7S2.ATCTCTAAAACGGACACT  0.059342  0.188810  0.099796  0.055628  0.020176   
Liver7S2.ATGCTTGGACATATTCCA  0.035437  0.202015  0.092842  0.046172  0.003542   
...                               ...       ...       ...       ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA    0.020380  0.132558  0.113974  0.032230  0.000000   
ICC3AD.AAGCGGGTCGGTGCAGGA    0.018243  0.121937  0.076972  0.038008  0.000000   
ICC3AD.ATCTCTGGACATAAGTAC    0.020901  0.112520  0.050096  0.051057  0.000000   
ICC3AD.CTGTGTACTTATGACACT    0.054618  0.171223  0.129313  0.060380  0.016675   
ICC3AD.TGCGGATATTGTAGTTTA    0.019285  0.160662  0.070127  0.041853  0.000000   

Regulon                       BCL6(+)  BHLHE40(+)  CEBPB(+)  CEBPD(+)  \
Cell                                                                    
Liver7S2.TTCATAAGATGGTAGAGA  0.019256    0.074477  0.194087  0.202787   
Liver7S2.TCGTAAAAAACGCCGACG  0.000000    0.084160  0.239348  0.183016   
Liver7S2.GCAGGAGCTCAAACGAGC  0.000000    0.063887  0.224479  0.150145   
Liver7S2.ATCTCTAAAACGGACACT  0.000000    0.082764  0.206466  0.110770   
Liver7S2.ATGCTTGGACATATTCCA  0.020275    0.077951  0.187278  0.154572   
...                               ...         ...       ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA    0.000000    0.040409  0.095044  0.101406   
ICC3AD.AAGCGGGTCGGTGCAGGA    0.000000    0.025500  0.057611  0.036181   
ICC3AD.ATCTCTGGACATAAGTAC    0.000000    0.034437  0.088627  0.090822   
ICC3AD.CTGTGTACTTATGACACT    0.000000    0.038126  0.046570  0.045259   
ICC3AD.TGCGGATATTGTAGTTTA    0.000000    0.046399  0.047547  0.121272   

Regulon                      CEBPZ(+)  ...  TFDP1(+)  TGIF1(+)   USF2(+)  \
Cell                                   ...                                 
Liver7S2.TTCATAAGATGGTAGAGA       0.0  ...  0.006727  0.000000  0.052508   
Liver7S2.TCGTAAAAAACGCCGACG       0.0  ...  0.024562  0.000000  0.076838   
Liver7S2.GCAGGAGCTCAAACGAGC       0.0  ...  0.006687  0.000000  0.062341   
Liver7S2.ATCTCTAAAACGGACACT       0.0  ...  0.009247  0.000000  0.062046   
Liver7S2.ATGCTTGGACATATTCCA       0.0  ...  0.002758  0.000000  0.051886   
...                               ...  ...       ...       ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA         0.0  ...  0.000000  0.000000  0.022776   
ICC3AD.AAGCGGGTCGGTGCAGGA         0.0  ...  0.002678  0.000000  0.030466   
ICC3AD.ATCTCTGGACATAAGTAC         0.0  ...  0.000000  0.000000  0.024901   
ICC3AD.CTGTGTACTTATGACACT         0.0  ...  0.031374  0.137278  0.027630   
ICC3AD.TGCGGATATTGTAGTTTA         0.0  ...  0.008942  0.000000  0.024002   

Regulon                       XBP1(+)    YY1(+)  ZBTB4(+)  ZBTB5(+)  ZMIZ1(+)  \
Cell                                                                            
Liver7S2.TTCATAAGATGGTAGAGA  0.030303  0.041027  0.030172  0.000000  0.037004   
Liver7S2.TCGTAAAAAACGCCGACG  0.061546  0.037569  0.000000  0.041897  0.032324   
Liver7S2.GCAGGAGCTCAAACGAGC  0.022646  0.021988  0.000000  0.000000  0.051447   
Liver7S2.ATCTCTAAAACGGACACT  0.074605  0.021083  0.035671  0.000000  0.018064   
Liver7S2.ATGCTTGGACATATTCCA  0.044588  0.036193  0.115630  0.108966  0.058879   
...                               ...       ...       ...       ...       ...   
ICC3AD.CCGCTAGCTGTGAACCTA    0.037767  0.037746  0.000000  0.000000  0.037645   
ICC3AD.AAGCGGGTCGGTGCAGGA    0.070297  0.026220  0.000000  0.000000  0.037671   
ICC3AD.ATCTCTGGACATAAGTAC    0.010858  0.011828  0.000000  0.000000  0.042128   
ICC3AD.CTGTGTACTTATGACACT    0.033836  0.014202  0.000000  0.000000  0.051132   
ICC3AD.TGCGGATATTGTAGTTTA    0.0047

In [30]:
anno=pd.read_csv("/media/ggj/ggjlab2/hezuo/gwh/myeloid/pseudocell/macrophage_anno.csv",index_col=0)

In [31]:
anno

NA         CellType
Liver7S2.TTCATAAGATGGTAGAGA  Liver7S2.TTCATAAGATGGTAGAGA     Kupffer cell
Liver7S2.TCGTAAAAAACGCCGACG  Liver7S2.TCGTAAAAAACGCCGACG     Kupffer cell
Liver7S2.GCAGGAGCTCAAACGAGC  Liver7S2.GCAGGAGCTCAAACGAGC     Kupffer cell
Liver7S2.ATCTCTAAAACGGACACT  Liver7S2.ATCTCTAAAACGGACACT     Kupffer cell
Liver7S2.ATGCTTGGACATATTCCA  Liver7S2.ATGCTTGGACATATTCCA     Kupffer cell
...                                                  ...              ...
ICC3AD.CCGCTAGCTGTGAACCTA      ICC3AD.CCGCTAGCTGTGAACCTA       Macrophage
ICC3AD.AAGCGGGTCGGTGCAGGA      ICC3AD.AAGCGGGTCGGTGCAGGA  Macropahge_CLU+
ICC3AD.ATCTCTGGACATAAGTAC      ICC3AD.ATCTCTGGACATAAGTAC  Macropahge_CLU+
ICC3AD.CTGTGTACTTATGACACT      ICC3AD.CTGTGTACTTATGACACT  Macropahge_CLU+
ICC3AD.TGCGGATATTGTAGTTTA      ICC3AD.TGCGGATATTGTAGTTTA  Macropahge_CLU+

[17626 rows x 2 columns]

In [32]:
rss = regulon_specificity_scores(auc_mtx, anno['CellType'])
rss

AHR(+)   ATF3(+)   ATF4(+)   ATF5(+)  BACH1(+)   BCL6(+)  \
Kupffer cell       0.430460  0.450209  0.458837  0.452536  0.394762  0.298121   
Macropahge_FABP5+  0.430843  0.449154  0.434117  0.452577  0.331953  0.283396   
Macrophage         0.266237  0.274414  0.274716  0.266372  0.228695  0.204107   
Macropahge_CLU+    0.319845  0.327628  0.331006  0.325534  0.271662  0.277920   

                   BHLHE40(+)  CEBPB(+)  CEBPD(+)  CEBPZ(+)  ...  TFDP1(+)  \
Kupffer cell         0.522782  0.536902  0.528720  0.213085  ...  0.442828   
Macropahge_FABP5+    0.416457  0.413718  0.398647  0.208183  ...  0.373593   
Macrophage           0.250788  0.245399  0.257829  0.182595  ...  0.250556   
Macropahge_CLU+      0.298189  0.286060  0.295701  0.197302  ...  0.306504   

                   TGIF1(+)   USF2(+)   XBP1(+)    YY1(+)  ZBTB4(+)  ZBTB5(+)  \
Kupffer cell       0.238038  0.514616  0.473756  0.515638  0.389619  0.288792   
Macropahge_FABP5+  0.331059  0.421229  0.407193  0.396483  0.228152  0.228641   
Macrophage         0.211836  0.254117  0.256902  0.257595  0.190752  0.194357   
Macropahge_CLU+    0.252018  0.299495  0.329761  0.308359  0.209198  0.214095   

                   ZMIZ1(+)  ZNF282(+)  ZNF471(+)  
Kupffer cell       0.467249   0.232613   0.479096  
Macropahge_FABP5+  0.447087   0.221194   0.393135  
Macrophage         0.261963   0.195127   0.281733  
Macropahge_CLU+    0.320415   0.218544   0.323578  

[4 rows x 98 columns]

In [33]:
rss.to_csv("/media/ggj/ggjlab2/hezuo/gwh/myeloid/pseudocell/results/rss.type.csv")

In [11]:
rss=pd.read_csv("./results/rss.type.csv",index_col=0)
rss

AHR(+)   ATF3(+)   ATF4(+)   ATF5(+)  BACH1(+)   BCL6(+)  \
Kupffer cell       0.430460  0.450209  0.458837  0.452536  0.394762  0.298121   
Macropahge_FABP5+  0.430843  0.449154  0.434117  0.452577  0.331953  0.283396   
Macrophage         0.266237  0.274414  0.274716  0.266372  0.228695  0.204107   
Macropahge_CLU+    0.319845  0.327628  0.331006  0.325534  0.271662  0.277920   

                   BHLHE40(+)  CEBPB(+)  CEBPD(+)  CEBPZ(+)  ...  TFDP1(+)  \
Kupffer cell         0.522782  0.536902  0.528720  0.213085  ...  0.442828   
Macropahge_FABP5+    0.416457  0.413718  0.398647  0.208183  ...  0.373593   
Macrophage           0.250788  0.245399  0.257829  0.182595  ...  0.250556   
Macropahge_CLU+      0.298189  0.286060  0.295701  0.197302  ...  0.306504   

                   TGIF1(+)   USF2(+)   XBP1(+)    YY1(+)  ZBTB4(+)  ZBTB5(+)  \
Kupffer cell       0.238038  0.514616  0.473756  0.515638  0.389619  0.288792   
Macropahge_FABP5+  0.331059  0.421229  0.407193  0.396483  0.228152  0.228641   
Macrophage         0.211836  0.254117  0.256902  0.257595  0.190752  0.194357   
Macropahge_CLU+    0.252018  0.299495  0.329761  0.308359  0.209198  0.214095   

                   ZMIZ1(+)  ZNF282(+)  ZNF471(+)  
Kupffer cell       0.467249   0.232613   0.479096  
Macropahge_FABP5+  0.447087   0.221194   0.393135  
Macrophage         0.261963   0.195127   0.281733  
Macropahge_CLU+    0.320415   0.218544   0.323578  

[4 rows x 98 columns]